<a href="https://colab.research.google.com/github/rdaniello/DataVizFall2020_Colab/blob/master/Lecture_091620_Assigment.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import pandas as pd
import folium
import numpy as np

In [ ]:
# https://github.com/nytimes/covid-19-data repository location
db = "https://raw.githubusercontent.com/nytimes/covid-19-data/master/us-counties.csv"
df = pd.read_csv(db)
df.head(1)

df['date'] = pd.to_datetime(df['date'])
df.dtypes

date      datetime64[ns]
county            object
state             object
fips             float64
cases              int64
deaths             int64
dtype: object

In [ ]:
# function to filter by date and group and sum by state
def covid_stat_on(df,strDate, m_type):
    # date filter
    df_temp = df[df['date']==strDate][['state', m_type]].copy().dropna().reset_index(drop=True)

    # state sum
    df_temp = df_temp.groupby(by=['state']).sum()
    df_temp['state_name'] = df_temp.index

    # use log of cases total
    df_temp['cases'] = np.log(df_temp[m_type])
                                    
    return df_temp

covid_stat_on(df,'2020-9-15', 'deaths').head(1)

/usr/local/lib/python3.6/dist-packages/pandas/core/series.py:679: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)


deaths state_name     cases
state                               
Alabama    2387    Alabama  7.777793

In [ ]:
# the GEOJSON file
cb_2018_us_state_5m = "https://raw.githubusercontent.com/rdaniello/DataVizFall2020_Colab/master/cb_2018_us_state_5m.json"

tmp_f = pd.read_json(cb_2018_us_state_5m)


In [117]:
#Map object 
m = folium.Map(
            location=[48, -102], # center the map to this point
            zoom_start=4)        # starting zoom!

#Choropleth layer - data function returns log of cases
folium.Choropleth(
    geo_data=cb_2018_us_state_5m, ## load the downloaded GeoJSON (mapshaper.org converted)
    name='Covid-19 State Cases',          ## add a name for the layer
    legend_name='Actual State Covid-19 Cases (log)',  ## add legend topic
    data=covid_stat_on(df,'2020-9-13', 'cases'),   ## pass our covid-19 data to the layer method
    columns=['state_name','cases'],             ## the columns from our data
    key_on='feature.properties.NAME',    ## the state
    fill_color='YlOrRd',                    ## color style BuGn, BuPu, GnBu, OrRd, PuBu, PuBuGn, PuRd, RdPu, YlGn, YlGnBu, YlOrBr, and YlOrRd
    bins=9,                               ## number of bins usef of color codding 
    fill_opacity=0.7,
    line_opacity=0.2,
    nan_fill_color='blue',
    highlight=True,
    show=False
).add_to(m)

choropleth = folium.Choropleth(
    geo_data=cb_2018_us_state_5m,
    name='Covid-19 State Deaths',
    legend_name='Actual State Covid-19 Deaths (log)',
    data=covid_stat_on(df,'2020-9-13', 'deaths'),
    columns=['state_name','deaths'],
    key_on='feature.properties.NAME',
    fill_color='YlGnBu',
    bins=9,
    fill_opacity=0.7,
    line_opacity=0.2,
    nan_fill_color='none',
    highlight=True,
     show=True).add_to(m)

folium.LayerControl().add_to(m)

m

/usr/local/lib/python3.6/dist-packages/pandas/core/series.py:679: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)


In [ ]:
m.save('index.html')